# `Series`

La structure de données `Series` est une structure de type tableau mono-dimensionnel indicé. Toutes les données du tableau doivent être du même type mais ce type est quelconque (`int`, `float`, `string`, `object`, ...). Chaque valeur possède un indice ou label qui sera appelé `index`. Cela généralise en quelque sorte les `ndarray` de `numpy` et les dictionnaires dont la clé est quelconque.

In [1]:
import numpy as np
import pandas as pd

gen = np.random.default_rng() 

## Création d'une Serie

Pour créer une série, il est possible d'utiliser la fonction `Series` du module `pandas` avec pour argument un dictionnaire, un `ndarray`, une `list`, un objet itérable, une valeur scalaire.

L'index est un argument optionnel qui, lorsqu'il est donné, doit être un objet hashable et de la même taille que celle des données.

Voici un exemple.

In [3]:
# help(pd.Series)

In [5]:
N = 4
print(gen.random((N,)))

[0.50767064 0.13246059 0.24536329 0.06682863]


In [7]:
print(
    pd.Series(gen.random(N,))
)

0    0.497305
1    0.099055
2    0.293137
3    0.933276
dtype: float64


In [16]:
display(
    pd.Series(gen.random((N,)), index=np.arange(1, N+1))
)

1    0.392402
2    0.992652
3    0.796755
4    0.848890
dtype: float64

In [17]:
display(
    pd.Series(
    {
        k: gen.random() for k in range(1, N+1)
    })
)

1    0.430083
2    0.644207
3    0.553739
4    0.546260
dtype: float64

In [7]:
display(
    pd.Series(gen.random(), index=range(N))
)

0    0.04174
1    0.04174
2    0.04174
3    0.04174
dtype: float64

## Utilisation d'une `Serie` comme un `ndarray`

Une série peut s'utiliser comme un tableau `numpy`. C'est-à-dire que l'on peut 
- accéder en lecture et en écriture aux données en utilisant des `slices` avec les deux points (`:`)
- faire des opérations mathématiques sur tout le tableau à l'aide d'une seule commande (sans boucle écrite en python).

In [27]:
s = pd.Series(gen.random((N,)), index=np.arange(1,N+1))
print(s)

1    0.649653
2    0.423986
3    0.782005
4    0.948255
dtype: float64


__Accès à un seul élément à l'aide de l'opérateur `iat[]`__

In [28]:
print(s.iat[0])
print(s.iat[-1])
dummy = s.iat[1]
s.iat[1] = np.nan
print(s)
s.iat[1] = dummy

0.6496534143568643
0.9482550393507959
1    0.649653
2         NaN
3    0.782005
4    0.948255
dtype: float64


__Accès à plusieurs éléments à l'aide de l'opérateur `iloc`__ 

In [29]:
dummy = np.array(s.iloc[:])  # copy des données dans un ndarray
# dummy = s.iloc[:].to_numpy()  # ne marche pas : données au même endroit !
print(type(dummy))
s.iloc[1:-1] = np.nan
print(s)
s.iloc[:] = dummy
print(s)

<class 'numpy.ndarray'>
1    0.649653
2         NaN
3         NaN
4    0.948255
dtype: float64
1    0.649653
2    0.423986
3    0.782005
4    0.948255
dtype: float64


__Exemples d'opérations__

In [30]:
print(s+1)
print(np.exp(s))

1    1.649653
2    1.423986
3    1.782005
4    1.948255
dtype: float64
1    1.914877
2    1.528040
3    2.185851
4    2.581202
dtype: float64


In [32]:
print(s.mean())
print(s > s.mean())

0.7009749216592733
1    False
2    False
3     True
4     True
dtype: bool


Il est possible de récupérer un objet de type `ndarray` à partir des données d'une `Serie`. __Attention__, ce n'est pas une copie...

In [33]:
dummy = np.array(s.iloc[:])
tbl = s.to_numpy()
print(type(tbl))
tbl[1:-1] = np.nan
print(s)
s.iloc[:] = dummy

<class 'numpy.ndarray'>
1    0.649653
2         NaN
3         NaN
4    0.948255
dtype: float64


## Utilisation d'une `Serie` comme un dictionnaire `dict`

Une série `Serie` est également utilisable comme un dictionnaire dont la taille est fixe. Les données sont accessibles en lecture et en écriture à l'aide de l'index ou label.

<div class="alert alert-block alert-info">
    <b>Warning</b> : pour être complet, notez que les labels ne sont pas nécessairement uniques ce qui peut parfois préter à confusion. Faites attention à ce point car une erreur est vite arrivée. Nous utiliserons le plus souvent des indices uniques pour éviter ces problèmes.
</div>

In [47]:
from string import ascii_letters
print(ascii_letters)
N = 15
s = pd.Series(gen.random((N,)), index=list(ascii_letters[:N]))
print(s)

abcdefghijklmnopqrstuvwxyzABCDEFGHIJKLMNOPQRSTUVWXYZ
a    0.292473
b    0.547676
c    0.265124
d    0.132766
e    0.991677
f    0.964381
g    0.318358
h    0.931198
i    0.105173
j    0.481224
k    0.285238
l    0.232295
m    0.909324
n    0.738164
o    0.710724
dtype: float64


__Accès à un seul élément à l'aide de l'opérateur `at[]`__

In [36]:
print(s.at['a'])
print(s.at['d'])
dummy = s.at['b']
s.at['b'] = np.nan
print(s)
s.at['b'] = dummy

0.17322944338366486
0.01806488998206124
a    0.173229
b         NaN
c    0.940278
d    0.018065
dtype: float64


Comme dans un dictionnaire, lorsque la valeur correspondant au label demandé n'existe pas, il y a un message d'erreur. On peut éviter cette erreur et retourner une valeur choisie en utilisant la fonction `get`.

In [38]:
# print(s.at['f'])
print(s.get('f', np.nan))
print(s.get('a', np.nan))

nan
0.43506113511776723


__Accès à plusieurs éléments à l'aide de l'opérateur `loc`__ 

Remarquez que l'utilisation des `slices` est possible mais fonctionne légèrement différemment : le premier terme et le dernier sont inclus.

In [44]:
s2 = pd.Series(gen.random((10,)))
print(s2.iloc[1:9])
print(s2.loc[1:9])

1    0.960317
2    0.253942
3    0.834235
4    0.653088
5    0.544806
6    0.376675
7    0.542966
8    0.011867
dtype: float64
1    0.960317
2    0.253942
3    0.834235
4    0.653088
5    0.544806
6    0.376675
7    0.542966
8    0.011867
9    0.699496
dtype: float64


In [45]:
dummy = np.array(s.loc[:])  # copy des données dans un ndarray
s.loc["b":"c"] = np.nan
print(s)
s.loc[:] = dummy

a    0.435061
b         NaN
c         NaN
d    0.641885
dtype: float64


Comme pour les tableaux `numpy`, il est possible de prendre une partie de la série correspondant à un critère à l'aide d'une autre série de booléens (ayant les mêmes labels). Voici un exemple important que l'on utilisera souvent.

In [49]:
mask1 = s > s.median()
mask2 = s > .5
print(mask1 * mask2)
print(s.loc[mask1 + mask2])

a    False
b     True
c    False
d    False
e     True
f     True
g    False
h     True
i    False
j    False
k    False
l    False
m     True
n     True
o     True
dtype: bool
b    0.547676
e    0.991677
f    0.964381
h    0.931198
m    0.909324
n    0.738164
o    0.710724
dtype: float64


## Donnons un nom à une `Serie`

Il est possible d'ajouter un nom à une série. Attention, lorsque la série est renommée, il y a une création d'un nouvel objet : les données et les indices sont des tableaux stockés dans des emplacements différents !

In [50]:
s = pd.Series(
    gen.random((N,)),
    index=list(ascii_letters[:N]),
    name="Ma première série"
)
print(s)

a    0.691633
b    0.234427
c    0.989501
d    0.792712
e    0.141640
f    0.971444
g    0.846010
h    0.084188
i    0.657985
j    0.879149
k    0.363479
l    0.599823
m    0.895487
n    0.327551
o    0.318575
Name: Ma première série, dtype: float64


In [51]:
s.rename("Nouveau nom")
print(s)

a    0.691633
b    0.234427
c    0.989501
d    0.792712
e    0.141640
f    0.971444
g    0.846010
h    0.084188
i    0.657985
j    0.879149
k    0.363479
l    0.599823
m    0.895487
n    0.327551
o    0.318575
Name: Ma première série, dtype: float64


In [52]:
s2 = s.rename("Ma deuxième série")
print(s2)

a    0.691633
b    0.234427
c    0.989501
d    0.792712
e    0.141640
f    0.971444
g    0.846010
h    0.084188
i    0.657985
j    0.879149
k    0.363479
l    0.599823
m    0.895487
n    0.327551
o    0.318575
Name: Ma deuxième série, dtype: float64


In [53]:
cmp_add = lambda obj1, obj2: hex(id(obj1)) == hex(id(obj2))
print(f"Les objets sont ils les mêmes : {cmp_add(s, s2)}")
print(f"Les données sont elles les mêmes : {cmp_add(s.array, s2.array)}")
print(f"Les labels sont ils les mêmes : {cmp_add(s.index, s2.index)}")
s2.iloc[:] = np.nan
print(s)
print(s2)

Les objets sont ils les mêmes : False
Les données sont elles les mêmes : False
Les labels sont ils les mêmes : False
a    0.691633
b    0.234427
c    0.989501
d    0.792712
e    0.141640
f    0.971444
g    0.846010
h    0.084188
i    0.657985
j    0.879149
k    0.363479
l    0.599823
m    0.895487
n    0.327551
o    0.318575
Name: Ma première série, dtype: float64
a   NaN
b   NaN
c   NaN
d   NaN
e   NaN
f   NaN
g   NaN
h   NaN
i   NaN
j   NaN
k   NaN
l   NaN
m   NaN
n   NaN
o   NaN
Name: Ma deuxième série, dtype: float64


In [55]:
print(s.name)
s.name = "tets"
print(s)

Ma première série
a    0.691633
b    0.234427
c    0.989501
d    0.792712
e    0.141640
f    0.971444
g    0.846010
h    0.084188
i    0.657985
j    0.879149
k    0.363479
l    0.599823
m    0.895487
n    0.327551
o    0.318575
Name: tets, dtype: float64


In [56]:
help(s.rename)

Help on method rename in module pandas.core.series:

rename(index: 'Renamer | Hashable | None' = None, *, axis: 'Axis | None' = None, copy: 'bool | None' = None, inplace: 'bool' = False, level: 'Level | None' = None, errors: 'IgnoreRaise' = 'ignore') -> 'Series | None' method of pandas.core.series.Series instance
    Alter Series index labels or name.
    
    Function / dict values must be unique (1-to-1). Labels not contained in
    a dict / Series will be left as-is. Extra labels listed don't throw an
    error.
    
    Alternatively, change ``Series.name`` with a scalar value.
    
    See the :ref:`user guide <basics.rename>` for more.
    
    Parameters
    ----------
    index : scalar, hashable sequence, dict-like or function optional
        Functions or dict-like are transformations to apply to
        the index.
        Scalar or hashable sequence-like will alter the ``Series.name``
        attribute.
    axis : {0 or 'index'}
        Unused. Parameter needed for compatibi